In [1]:
import json
from neo4j import GraphDatabase
import pandas as pd
import random
from pprint import pprint

# Test Neo4j connection

In [2]:
# test connection.
# must open Neo4j and click start on project
# returns 1 if connection established.

# Create a driver
uri = "bolt://localhost:7687"  # replace with your Neo4j instance URI
username = "neo4j"  # replace with your username

# password should be unique between projects to ensure the correct project is updated.
password = "aylien_business_P29213nm,."  # replace with your DBMS password.
driver = GraphDatabase.driver(uri, auth=(username, password))

# Open a new session
with driver.session() as session:
    # Run a simple test query
    result = session.run("RETURN 1")
    print(result.single()[0])  # should print 1

# Close the driver
driver.close()


1


# Create cypher queries from JSON results file

In [17]:
with open("./results/PP_reformatted_aylien_business_5k_responses.json") as f:
    data = json.load(f)

cypher_queries = []

for entry in data:
    # Trim empty spaces from keys
    entry = {key.strip(): value for key, value in entry.items()}
    
    if 'org' not in entry or not entry['org']:
        continue
    
    # Skip if org contains ';' or is only 'NA' or 'na'
    if ';' in entry['org'] or entry['org'].strip().upper() == 'NA':
        continue

    try:
        params = {
            'org': entry['org'],
            'article_id': entry['article_id'],
            'country': [item.strip() for item in entry['country'].split(';')] if entry['country'] else None,
            'state': [item.strip() for item in entry['state'].split(';')] if entry['state'] else None,
            'city': [item.strip() for item in entry['city'].split(';')] if entry['city'] else None,
            'industry': [item.strip() for item in entry['industry'].split(';')] if entry['industry'] else None,
            'risks': [item.strip() for item in entry['risks'].split(';')] if entry['risks'] else None,
            'items_sold': [item.strip() for item in entry['items_sold'].split(';')] if entry['items_sold'] else None,
            'service_provided': [service.strip() for service in entry['service_provided'].split(';')] if entry['service_provided'] else None,
            'business_relations': [relation.strip() for relation in entry['business_relations'].split(';')] if entry['business_relations'] else None,
            'source': entry['source']
        }
    except KeyError:
        continue

    # Handle organization
    cypher_queries.append(('''
        MERGE (o:Organisation {name: $org})
        ON CREATE SET o.article_ids = [$article_id]
        ON MATCH SET o.article_ids = coalesce(o.article_ids, []) + [$article_id]
    ''', {'org': params['org'], 'article_id': params['article_id']}))

    # Handle country
    if params['country']:
        for country in params['country']:
            cypher_queries.append(('''
                MERGE (cou:Country {name: $country})
                ON CREATE SET cou.article_ids = [$article_id]
                ON MATCH SET cou.article_ids = coalesce(cou.article_ids, []) + [$article_id]
                WITH cou
                MATCH (o:Organisation {name: $org})
                MERGE (o)-[:AT_COUNTRY]->(cou)
            ''', {'org': params['org'], 'country': country, 'article_id': params['article_id']}))

    # Handle state
    if params['state']:
        for state in params['state']:
            cypher_queries.append(('''
                MERGE (sta:State {name: $state})
                ON CREATE SET sta.article_ids = [$article_id]
                ON MATCH SET sta.article_ids = coalesce(sta.article_ids, []) + [$article_id]
                WITH sta
                MATCH (o:Organisation {name: $org})
                MERGE (o)-[:AT_STATE]->(sta)
            ''', {'org': params['org'], 'state': state, 'article_id': params['article_id']}))

    # Handle city
    if params['city']:
        for city in params['city']:
            cypher_queries.append(('''
                MERGE (cit:City {name: $city})
                ON CREATE SET cit.article_ids = [$article_id]
                ON MATCH SET cit.article_ids = coalesce(cit.article_ids, []) + [$article_id]
                WITH cit
                MATCH (o:Organisation {name: $org})
                MERGE (o)-[:AT_CITY]->(cit)
            ''', {'org': params['org'], 'city': city, 'article_id': params['article_id']}))

    # Handle industry
    if params['industry']:
        for industry in params['industry']:
            cypher_queries.append(('''
                MERGE (ind:Industry {name: $industry})
                ON CREATE SET ind.article_ids = [$article_id]
                ON MATCH SET ind.article_ids = coalesce(ind.article_ids, []) + [$article_id]
                WITH ind
                MATCH (o:Organisation {name: $org})
                MERGE (o)-[:IN_INDUSTRY]->(ind)
            ''', {'org': params['org'], 'industry': industry, 'article_id': params['article_id']}))

    # Handle risks
    if params['risks']:
        for risk in params['risks']:
            cypher_queries.append(('''
                MERGE (r:Risk {name: $risk})
                ON CREATE SET r.article_ids = [$article_id]
                ON MATCH SET r.article_ids = coalesce(r.article_ids, []) + [$article_id]
                WITH r
                MATCH (o:Organisation {name: $org})
                MERGE (o)-[:FACING_RISK]->(r)
            ''', {'org': params['org'], 'risk': risk, 'article_id': params['article_id']}))

    # Handle items sold
    if params['items_sold']:
        for item in params['items_sold']:
            cypher_queries.append(('''
                MATCH (o:Organisation {name: $org})
                MERGE (i:Item {name: $item})
                ON CREATE SET i.article_ids = [$article_id]
                ON MATCH SET i.article_ids = coalesce(i.article_ids, []) + [$article_id]
                MERGE (o)-[:SELLING_ITEM]->(i)
            ''', {'org': params['org'], 'item': item, 'article_id': params['article_id']}))

    # Handle services provided
    if params['service_provided']:
        for service in params['service_provided']:
            cypher_queries.append(('''
                MATCH (o:Organisation {name: $org})
                MERGE (s:Service {name: $service})
                ON CREATE SET s.article_ids = [$article_id]
                ON MATCH SET s.article_ids = coalesce(s.article_ids, []) + [$article_id]
                MERGE (o)-[:PROVIDING_SERVICE]->(s)
            ''', {'org': params['org'], 'service': service, 'article_id': params['article_id']}))

    # Handle business relations
    if params['business_relations']:
        for relation in params['business_relations']:
            cypher_queries.append(('''
                MATCH (o:Organisation {name: $org})
                MERGE (br:Organisation {name: $relation})
                ON CREATE SET br.article_ids = [$article_id]
                ON MATCH SET br.article_ids = coalesce(br.article_ids, []) + [$article_id]
                MERGE (o)-[:IN_BUSINESS_WITH]->(br)
            ''', {'org': params['org'], 'relation': relation, 'article_id': params['article_id']}))

In [18]:
print(len(cypher_queries))

with open("./results/cypher_queries/cypher_queries_aylien_business_5k_responses.json", "w") as file:
    json.dump(cypher_queries, file, indent=4)

cypher_queries

17783


[('\n        MERGE (o:Organisation {name: $org})\n        ON CREATE SET o.article_ids = [$article_id]\n        ON MATCH SET o.article_ids = coalesce(o.article_ids, []) + [$article_id]\n    ',
  {'org': 'Nike Inc.', 'article_id': 5709294677}),
 ('\n                MERGE (ind:Industry {name: $industry})\n                ON CREATE SET ind.article_ids = [$article_id]\n                ON MATCH SET ind.article_ids = coalesce(ind.article_ids, []) + [$article_id]\n                WITH ind\n                MATCH (o:Organisation {name: $org})\n                MERGE (o)-[:IN_INDUSTRY]->(ind)\n            ',
  {'org': 'Nike Inc.',
   'industry': 'Athletic apparel',
   'article_id': 5709294677}),
 ('\n                MERGE (r:Risk {name: $risk})\n                ON CREATE SET r.article_ids = [$article_id]\n                ON MATCH SET r.article_ids = coalesce(r.article_ids, []) + [$article_id]\n                WITH r\n                MATCH (o:Organisation {name: $org})\n                MERGE (o)-[:

# Feed cypher queries into Neo4j directly to create KG

In [19]:
# Create a function to execute the Cypher queries
def execute_queries(queries):
    # Establish a connection to Neo4j
    uri = "bolt://localhost:7687"  # replace with your Neo4j instance URI
    username = "neo4j"  # replace with your username
    password = "aylien_business_P29213nm,."  # replace with your DBMS password
    driver = GraphDatabase.driver(uri, auth=(username, password))

    # Start a session
    with driver.session() as session:
        # Execute each query with its parameters
        for query, parameters in queries:
            print("Query:", query)
            print("Parameters:", parameters)
            session.run(query, **parameters)

    # Close the driver
    driver.close()

# Execute the Cypher queries
execute_queries(cypher_queries)


Query: 
        MERGE (o:Organisation {name: $org})
        ON CREATE SET o.article_ids = [$article_id]
        ON MATCH SET o.article_ids = coalesce(o.article_ids, []) + [$article_id]
    
Parameters: {'org': 'Nike Inc.', 'article_id': 5709294677}
Query: 
                MERGE (ind:Industry {name: $industry})
                ON CREATE SET ind.article_ids = [$article_id]
                ON MATCH SET ind.article_ids = coalesce(ind.article_ids, []) + [$article_id]
                WITH ind
                MATCH (o:Organisation {name: $org})
                MERGE (o)-[:IN_INDUSTRY]->(ind)
            
Parameters: {'org': 'Nike Inc.', 'industry': 'Athletic apparel', 'article_id': 5709294677}
Query: 
                MERGE (r:Risk {name: $risk})
                ON CREATE SET r.article_ids = [$article_id]
                ON MATCH SET r.article_ids = coalesce(r.article_ids, []) + [$article_id]
                WITH r
                MATCH (o:Organisation {name: $org})
                MERGE (o)-[

Query: 
                MERGE (sta:State {name: $state})
                ON CREATE SET sta.article_ids = [$article_id]
                ON MATCH SET sta.article_ids = coalesce(sta.article_ids, []) + [$article_id]
                WITH sta
                MATCH (o:Organisation {name: $org})
                MERGE (o)-[:AT_STATE]->(sta)
            
Parameters: {'org': 'TBC', 'state': 'Florida', 'article_id': 5709256977}
Query: 
                MERGE (cit:City {name: $city})
                ON CREATE SET cit.article_ids = [$article_id]
                ON MATCH SET cit.article_ids = coalesce(cit.article_ids, []) + [$article_id]
                WITH cit
                MATCH (o:Organisation {name: $org})
                MERGE (o)-[:AT_CITY]->(cit)
            
Parameters: {'org': 'TBC', 'city': 'Palm Beach Gardens', 'article_id': 5709256977}
Query: 
                MERGE (ind:Industry {name: $industry})
                ON CREATE SET ind.article_ids = [$article_id]
                ON MATCH SET

Query: 
        MERGE (o:Organisation {name: $org})
        ON CREATE SET o.article_ids = [$article_id]
        ON MATCH SET o.article_ids = coalesce(o.article_ids, []) + [$article_id]
    
Parameters: {'org': 'Kia and Hyundai', 'article_id': 5709182798}
Query: 
                MERGE (ind:Industry {name: $industry})
                ON CREATE SET ind.article_ids = [$article_id]
                ON MATCH SET ind.article_ids = coalesce(ind.article_ids, []) + [$article_id]
                WITH ind
                MATCH (o:Organisation {name: $org})
                MERGE (o)-[:IN_INDUSTRY]->(ind)
            
Parameters: {'org': 'Kia and Hyundai', 'industry': 'Automotive', 'article_id': 5709182798}
Query: 
                MERGE (r:Risk {name: $risk})
                ON CREATE SET r.article_ids = [$article_id]
                ON MATCH SET r.article_ids = coalesce(r.article_ids, []) + [$article_id]
                WITH r
                MATCH (o:Organisation {name: $org})
                MERGE

Query: 
                MERGE (cit:City {name: $city})
                ON CREATE SET cit.article_ids = [$article_id]
                ON MATCH SET cit.article_ids = coalesce(cit.article_ids, []) + [$article_id]
                WITH cit
                MATCH (o:Organisation {name: $org})
                MERGE (o)-[:AT_CITY]->(cit)
            
Parameters: {'org': 'Transcenta Holding Limited', 'city': 'Suzhou (Headquarters and Discovery, Clinical and Translational Research Center), Hangzhou (Process and Product Development Center and Manufacturing Facility), Princeton (Clinical Development Center), Beijing, Shanghai, Guangzhou (Clinical Development Centers), Boston and Los Angeles (External Partnering Center)', 'article_id': 5709098257}
Query: 
                MERGE (ind:Industry {name: $industry})
                ON CREATE SET ind.article_ids = [$article_id]
                ON MATCH SET ind.article_ids = coalesce(ind.article_ids, []) + [$article_id]
                WITH ind
             

Query: 
                MERGE (ind:Industry {name: $industry})
                ON CREATE SET ind.article_ids = [$article_id]
                ON MATCH SET ind.article_ids = coalesce(ind.article_ids, []) + [$article_id]
                WITH ind
                MATCH (o:Organisation {name: $org})
                MERGE (o)-[:IN_INDUSTRY]->(ind)
            
Parameters: {'org': 'Macerich', 'industry': 'Real Estate Investment Trust (REIT)', 'article_id': 5708776226}
Query: 
                MERGE (r:Risk {name: $risk})
                ON CREATE SET r.article_ids = [$article_id]
                ON MATCH SET r.article_ids = coalesce(r.article_ids, []) + [$article_id]
                WITH r
                MATCH (o:Organisation {name: $org})
                MERGE (o)-[:FACING_RISK]->(r)
            
Parameters: {'org': 'Macerich', 'risk': 'pandemic', 'article_id': 5708776226}
Query: 
                MERGE (r:Risk {name: $risk})
                ON CREATE SET r.article_ids = [$article_id]
        

...

Query: 
                MERGE (r:Risk {name: $risk})
                ON CREATE SET r.article_ids = [$article_id]
                ON MATCH SET r.article_ids = coalesce(r.article_ids, []) + [$article_id]
                WITH r
                MATCH (o:Organisation {name: $org})
                MERGE (o)-[:FACING_RISK]->(r)
            
Parameters: {'org': 'United Hospital Supply Corp.', 'risk': 'regulatory', 'article_id': 5669065504}
Query: 
                MATCH (o:Organisation {name: $org})
                MERGE (i:Item {name: $item})
                ON CREATE SET i.article_ids = [$article_id]
                ON MATCH SET i.article_ids = coalesce(i.article_ids, []) + [$article_id]
                MERGE (o)-[:SELLING_ITEM]->(i)
            
Parameters: {'org': 'United Hospital Supply Corp.', 'item': 'steel cabinets', 'article_id': 5669065504}
Query: 
                MATCH (o:Organisation {name: $org})
                MERGE (i:Item {name: $item})
                ON CREATE SET i.article_i

Query: 
                MERGE (r:Risk {name: $risk})
                ON CREATE SET r.article_ids = [$article_id]
                ON MATCH SET r.article_ids = coalesce(r.article_ids, []) + [$article_id]
                WITH r
                MATCH (o:Organisation {name: $org})
                MERGE (o)-[:FACING_RISK]->(r)
            
Parameters: {'org': 'PETRONAS Gas Berhad (PGB)', 'risk': 'regulatory', 'article_id': 5668836313}
Query: 
                MATCH (o:Organisation {name: $org})
                MERGE (s:Service {name: $service})
                ON CREATE SET s.article_ids = [$article_id]
                ON MATCH SET s.article_ids = coalesce(s.article_ids, []) + [$article_id]
                MERGE (o)-[:PROVIDING_SERVICE]->(s)
            
Parameters: {'org': 'PETRONAS Gas Berhad (PGB)', 'service': 'Gas transportation and regasification', 'article_id': 5668836313}
Query: 
                MATCH (o:Organisation {name: $org})
                MERGE (br:Organisation {name: $relation

Query: 
                MERGE (cit:City {name: $city})
                ON CREATE SET cit.article_ids = [$article_id]
                ON MATCH SET cit.article_ids = coalesce(cit.article_ids, []) + [$article_id]
                WITH cit
                MATCH (o:Organisation {name: $org})
                MERGE (o)-[:AT_CITY]->(cit)
            
Parameters: {'org': 'Department for Education', 'city': 'London', 'article_id': 5668686349}
Query: 
                MERGE (ind:Industry {name: $industry})
                ON CREATE SET ind.article_ids = [$article_id]
                ON MATCH SET ind.article_ids = coalesce(ind.article_ids, []) + [$article_id]
                WITH ind
                MATCH (o:Organisation {name: $org})
                MERGE (o)-[:IN_INDUSTRY]->(ind)
            
Parameters: {'org': 'Department for Education', 'industry': 'Government', 'article_id': 5668686349}
Query: 
                MATCH (o:Organisation {name: $org})
                MERGE (br:Organisation {name: $r

Query: 
                MATCH (o:Organisation {name: $org})
                MERGE (s:Service {name: $service})
                ON CREATE SET s.article_ids = [$article_id]
                ON MATCH SET s.article_ids = coalesce(s.article_ids, []) + [$article_id]
                MERGE (o)-[:PROVIDING_SERVICE]->(s)
            
Parameters: {'org': 'SleekFlow', 'service': 'AI-powered customer engagement solution', 'article_id': 5668448722}
Query: 
                MATCH (o:Organisation {name: $org})
                MERGE (br:Organisation {name: $relation})
                ON CREATE SET br.article_ids = [$article_id]
                ON MATCH SET br.article_ids = coalesce(br.article_ids, []) + [$article_id]
                MERGE (o)-[:IN_BUSINESS_WITH]->(br)
            
Parameters: {'org': 'SleekFlow', 'relation': 'Tiger Global Capital', 'article_id': 5668448722}
Query: 
                MATCH (o:Organisation {name: $org})
                MERGE (br:Organisation {name: $relation})
              

Query: 
                MERGE (r:Risk {name: $risk})
                ON CREATE SET r.article_ids = [$article_id]
                ON MATCH SET r.article_ids = coalesce(r.article_ids, []) + [$article_id]
                WITH r
                MATCH (o:Organisation {name: $org})
                MERGE (o)-[:FACING_RISK]->(r)
            
Parameters: {'org': 'Target', 'risk': 'product defect', 'article_id': 5668136182}
Query: 
                MATCH (o:Organisation {name: $org})
                MERGE (i:Item {name: $item})
                ON CREATE SET i.article_ids = [$article_id]
                ON MATCH SET i.article_ids = coalesce(i.article_ids, []) + [$article_id]
                MERGE (o)-[:SELLING_ITEM]->(i)
            
Parameters: {'org': 'Target', 'item': 'candles', 'article_id': 5668136182}
Query: 
        MERGE (o:Organisation {name: $org})
        ON CREATE SET o.article_ids = [$article_id]
        ON MATCH SET o.article_ids = coalesce(o.article_ids, []) + [$article_id]
    
Par

# Exploratory analysis via Neo4j KG

In [7]:
# Create a function to execute the Cypher queries
def execute_queries(queries):
    # Establish a connection to Neo4j
    uri = "bolt://localhost:7687"  # replace with your Neo4j instance URI
    username = "neo4j"  # replace with your username
    password = "aylien_business_P29213nm,."  # replace with your DBMS password
    driver = GraphDatabase.driver(uri, auth=(username, password))

    # Placeholder for query results
    results = []

    # Start a session
    with driver.session() as session:
        # Execute each query with its parameters
        for query, parameters in queries:
            #print("Query:", query)
            #print("Parameters:", parameters)
            result = session.run(query, **parameters)
            # Store the result immediately as a list of records
            results.append(list(result))

    # Close the driver
    driver.close()

    return results

##Define the exploratory Cypher queries

In [8]:
#### ORGS ####
query_unique_organisations = '''
MATCH (o:Organisation)
RETURN COUNT(DISTINCT o) AS num_unique_organisations
'''
query_list_organisations = '''
MATCH (o:Organisation)
RETURN COLLECT(DISTINCT o.name) AS unique_organisations
'''

#### COUNTRIES ####
query_unique_countries = '''
MATCH (cou:Country)
RETURN COUNT(DISTINCT cou) AS num_unique_countries
'''
query_list_countries = '''
MATCH (cou:Country)
RETURN COLLECT(DISTINCT cou.name) AS unique_countries
'''

#### STATES ####
query_unique_states = '''
MATCH (sta:State)
RETURN COUNT(DISTINCT sta) AS num_unique_states
'''
query_list_states = '''
MATCH (sta:State)
RETURN COLLECT(DISTINCT sta.name) AS unique_states
'''

#### CITIES ####
query_unique_cities = '''
MATCH (cit:City)
RETURN COUNT(DISTINCT cit) AS num_unique_cities
'''
query_list_cities = '''
MATCH (cit:City)
RETURN COLLECT(DISTINCT cit.name) AS unique_cities
'''

#### INDUSTRIES ####
query_unique_industries = '''
MATCH (ind:Industry)
RETURN COUNT(DISTINCT ind) AS num_unique_industries
'''

query_list_industries = '''
MATCH (ind:Industry)
RETURN COLLECT(DISTINCT ind.name) AS unique_industries
'''


#### RISKS ####
query_unique_risks = '''
MATCH (r:Risk)
RETURN COUNT(DISTINCT r) AS num_unique_risks
'''

query_list_risks = '''
MATCH (r:Risk)
RETURN COLLECT(DISTINCT r.name) AS unique_risks
'''

#### SERVICES PROVIDED ####
query_unique_services_provided = '''
MATCH (s:Service)
RETURN COUNT(DISTINCT s) AS num_unique_services_provided
'''

query_list_services_provided = '''
MATCH (s:Service)
RETURN COLLECT(DISTINCT s.name) AS unique_services_provided
'''

#### BUSINESS RELATIONS ####
query_unique_business_relations = '''
MATCH (br:BusinessRelation)
RETURN COUNT(DISTINCT br) AS num_unique_business_relations
'''

query_list_business_relations = '''
MATCH (br:BusinessRelation)
RETURN COLLECT(DISTINCT br.name) AS unique_business_relations
'''

#### ITEMS SOLD ####
query_unique_items_sold = '''
MATCH (i:Item)
RETURN COUNT(DISTINCT i) AS num_unique_items_sold
'''

query_list_items_sold = '''
MATCH (i:Item)
RETURN COLLECT(DISTINCT i.name) AS unique_items_sold
'''


In [9]:
# summary statistics only:

# Combine the queries into a list
cypher_queries = [
    (query_unique_organisations, {}),
    #(query_list_organisations, {}),
    
    (query_unique_countries, {}),
    #(query_list_countries, {}),
    
    (query_unique_states, {}),
    #(query_list_states, {}),
    
    (query_unique_cities, {}),
    #(query_list_cities, {}),
    
    (query_unique_industries, {}),
    #(query_unique_industries, {}), 
    
    (query_unique_risks, {}),
    #(query_list_risks, {}),
    
    (query_unique_items_sold, {})
    #(query_list_items_sold, {})
    
    (query_unique_services_provided, {}),
    #(query_list_services_provided, {}),
    
    (query_unique_business_relations, {}),
    #(query_list_business_relations, {}),
    
]

# Execute the Cypher queries
query_results = execute_queries(cypher_queries)

# Process the summary statistics
summary_results = []
for result in query_results:
    for record in result:
        summary = ", ".join([f"{key}: {value}" for key, value in record.items()])
        summary_results.append(summary)

# Print the summary statistics
for i, summary in enumerate(summary_results, 1):
    print(summary)
    print()


num_unique_organisations: 2097

num_unique_countries: 86

num_unique_states: 105

num_unique_cities: 371

num_unique_risks: 1153

num_unique_industries: 878

num_unique_services_provided: 1994

num_unique_business_relations: 1430

num_unique_items_sold: 991



In [ ]:
# Execute the exploratory Cypher queries
exploratory_query_results = execute_queries([
    (query_unique_organisations, {}),
    (query_list_organisations, {}),
    
    (query_unique_countries, {}),
    (query_list_countries, {}),
    
    (query_unique_states, {}),
    (query_list_states, {}),
    
    (query_unique_cities, {}),
    (query_list_cities, {}),
    
    (query_unique_risks, {}),
    (query_list_risks, {}),
    
    (query_unique_services_provided, {}),
    (query_list_services_provided, {}),
    
    (query_unique_items_sold, {}),
    (query_list_items_sold, {})
])

# Get the summary statistics
num_unique_organisations = exploratory_query_results[0][0]['num_unique_organisations']
unique_organisations = exploratory_query_results[1][0]['unique_organisations']
unique_countries = exploratory_query_results[3][0]['unique_countries']
unique_states = exploratory_query_results[5][0]['unique_states']
unique_cities = exploratory_query_results[7][0]['unique_cities']
unique_risks = exploratory_query_results[9][0]['unique_risks']
unique_services_provided = exploratory_query_results[11][0]['unique_services_provided']
unique_items_sold = exploratory_query_results[13][0]['unique_items_sold']

# Select a random sample of 10 organisations
sample_organisations = random.sample(unique_organisations, k=min(10, len(unique_organisations)))

# Select a random sample of 10 items sold
sample_items_sold = random.sample(unique_items_sold, k=min(10, len(unique_items_sold)))

# Select a random sample of 10 services provided
sample_services_provided = random.sample(unique_services_provided, k=min(10, len(unique_services_provided)))

# Select a random sample of 10 risk types
sample_risks = random.sample(unique_risks, k=min(10, len(unique_risks)))

# Select a random sample of 10 countries
sample_countries = random.sample(unique_countries, k=min(10, len(unique_countries)))

# Select a random sample of 10 states
sample_states = random.sample(unique_states, k=min(10, len(unique_states)))

# Select a random sample of 10 cities
sample_cities = random.sample(unique_cities, k=min(10, len(unique_cities)))

# Pretty print the random samples
# print("10 randomly selected organisations:")
# pprint(sample_organisations)
# print("\n10 randomly selected items sold (not necessarily by the above companies):")
# pprint(sample_items_sold)
# print("\n10 randomly selected services provided (not necessarily by the above companies):")
# pprint(sample_services_provided)
# print("\n10 randomly selected risk types (not necessarily faced by the above companies):")
# pprint(sample_risks)
# print("\n10 randomly selected countries (not necessarily of the above companies):")
# pprint(sample_countries)
# print("\n10 randomly selected states (not necessarily of the above companies):")
# pprint(sample_states)
# print("\n10 randomly selected cities (not necessarily of the above companies):")
# pprint(sample_cities)


## Unique items in each slot

In [ ]:
# export unique orgs:

unique_organisations

# Convert the list to a DataFrame
unique_orgs = pd.DataFrame(unique_organisations, columns=['ORGS'])

# Export the DataFrame to an Excel file
unique_orgs.to_excel('./results/aylien_responses_summary/neo4j_unique_orgs.xlsx')